In [1]:
import numpy as np
import cirq

pi = np.pi

Define functions for gate construction

In [2]:
def PauliRotation(circuit, qubits, coefficient, PauliString, dt):
    """
    Applies epx(-i * coeff * dt) to corresponding qubits
    """
    pauli_list = [term[0] for term in PauliString]         
    qubit_indices = [int(term[1:]) for term in PauliString]   

    for i in range(len(pauli_list)):
        if pauli_list[i] == 'Y':
            circuit.append(cirq.S(qubits[qubit_indices[i]]))
            circuit.append(cirq.H(qubits[qubit_indices[i]]))
        elif pauli_list[i] == 'X':
            circuit.append(cirq.H(qubits[qubit_indices[i]]))

    for i in range(len(qubit_indices)):
        if i < len(qubit_indices)-1:
            circuit.append(cirq.CNOT(qubits[qubit_indices[i]], qubits[qubit_indices[i + 1]]))
    # Coefficient
    if not pauli_list:
        circuit.append(cirq.global_phase_operation(np.exp(-1j * coefficient * dt)))
    else: 
        circuit.append(cirq.rz(2 * coefficient * dt)(qubits[qubit_indices[-1]])) # BLIND GATE

    for i in range(len(qubit_indices) - 2, -1, -1):  # from 2nd last down to 0
        circuit.append(cirq.CNOT(qubits[qubit_indices[i]], qubits[qubit_indices[i + 1]]))

    # Undo the basis changes in reverse order
    for i in reversed(range(len(pauli_list))):
        if pauli_list[i] == 'Y':
            circuit.append(cirq.H(qubits[qubit_indices[i]]))
            circuit.append(cirq.S(qubits[qubit_indices[i]])**-1)  # S† gate (inverse of S)
        elif pauli_list[i] == 'X':
            circuit.append(cirq.H(qubits[qubit_indices[i]]))

Define Molecule

In [3]:
from openfermion import get_fermion_operator, jordan_wigner, get_sparse_operator
from openfermionpyscf import generate_molecular_hamiltonian
from pyscf import gto, scf

num_qubits = 4

# Hydrogen Chain MOLECULE
# num_hydrogens = 2
# distance = 1.2 
# atom_coordinates = [f"H {i * distance} 0 0" for i in range(num_hydrogens)]
# mol = gto.Mole()
# mol.atom =  "; ".join(atom_coordinates)
# mol.basis = 'sto-3g'
# mol.charge = 0
# mol.spin = num_hydrogens % 2
# mol.build()

# LiH MOLECULE
distance = 1.6
mol = gto.Mole()
mol.atom = f"Li 0 0 0; H 0 0 {distance}" # Lithium hydride molecule
mol.basis = "sto-3g" #'cc-pv5z' 'cc-pvqz'  #These are the different choices of atomic orbitals to include in the calculation
mol.charge = 0 #electric charge sector
mol.spin = 0 #S_z sector
mol.build()

# Perform Hartree-Fock calculation
mf = scf.RHF(mol)
mf.kernel()

# Generate the molecular Hamiltonian
mol_ham = generate_molecular_hamiltonian(mol.atom,
        mol.basis,
        multiplicity = mol.spin + 1,
        charge = mol.charge,
        n_active_electrons=2,
        n_active_orbitals=2
)

mol.ao_labels()

converged SCF energy = -7.86186476980865


['0 Li 1s    ',
 '0 Li 2s    ',
 '0 Li 2px   ',
 '0 Li 2py   ',
 '0 Li 2pz   ',
 '1 H 1s    ']

In [4]:
# Jordan-Wigner transformation
H_fermi = get_fermion_operator(mol_ham)
print("number of terms: " + str(len(H_fermi.terms)))

qubit_hamiltonian = jordan_wigner(H_fermi)     # Convert the fermionic Hamiltonian to a qubit Hamiltonian using Jordan-Wigner transformation

# Print the qubit Hamiltonian
print("Qubit Hamiltonian:")
print(qubit_hamiltonian)
print("number of terms: ", len(qubit_hamiltonian.terms))
print(len(qubit_hamiltonian.terms.items()))

# Step 5: (Optional) Convert to a sparse matrix for simulation
H_mat = get_sparse_operator(qubit_hamiltonian).toarray()

number of terms: 73
Qubit Hamiltonian:
(-3.8006076768459764+0j) [] +
(-0.002137377016341704+0j) [X0 X1 Y2 Y3] +
(0.002137377016341704+0j) [X0 Y1 Y2 X3] +
(-0.004844443306154697+0j) [X0 Z1 X2] +
(-0.0132612556867148+0j) [X0 Z1 X2 Z3] +
(0.0007670968646192311+0j) [X0 X2] +
(0.002137377016341704+0j) [Y0 X1 X2 Y3] +
(-0.002137377016341704+0j) [Y0 Y1 X2 X3] +
(-0.004844443306154697+0j) [Y0 Z1 Y2] +
(-0.0132612556867148+0j) [Y0 Z1 Y2 Z3] +
(0.0007670968646192311+0j) [Y0 Y2] +
(0.18330834423430795+0j) [Z0] +
(0.0007670968646192311+0j) [Z0 X1 Z2 X3] +
(0.0007670968646192311+0j) [Z0 Y1 Z2 Y3] +
(0.11344680274916535+0j) [Z0 Z1] +
(0.08829538599842374+0j) [Z0 Z2] +
(0.09043276301476544+0j) [Z0 Z3] +
(-0.004844443306154701+0j) [X1 Z2 X3] +
(-0.013261255686714797+0j) [X1 X3] +
(-0.004844443306154701+0j) [Y1 Z2 Y3] +
(-0.013261255686714797+0j) [Y1 Y3] +
(0.18330834423430795+0j) [Z1] +
(0.09043276301476544+0j) [Z1 Z2] +
(0.08829538599842374+0j) [Z1 Z3] +
(1.7703267431810716+0j) [Z2] +
(0.414641671714

Generate all JW Pauli terms

In [5]:
from openfermion.ops import FermionOperator
import itertools

In [6]:
fermion_ops = []

# 1. Quadratic terms: a_p^\dagger a_q
for p, q in itertools.product(range(num_qubits), repeat=2):
    term_str = f'{p}^ {q}'
    fermion_ops.append(FermionOperator(term_str, 1.0))

# 2. Quartic terms: a_p^\dagger a_q^\dagger a_r a_s
for p, q, r, s in itertools.product(range(num_qubits), repeat=4):
    term_str = f'{p}^ {q}^ {r} {s}'
    fermion_ops.append(FermionOperator(term_str, 1.0))

print(f"Generated {len(fermion_ops)} FermionOperator terms")

# Collect unique JW mappings
unique_jw_terms = set()

for op in fermion_ops:
    jw_op = jordan_wigner(op)
    # Each jw_op can have multiple Pauli strings (QubitOperator terms)
    for term in jw_op.terms:
        # Convert term to human-readable string, e.g., "X0 Y1 Z2"
        if term == ():  # identity
            term_str = "I" * num_qubits
        else:
            term_str = " ".join(f"{p[1]}{p[0]}" for p in term)
        unique_jw_terms.add(term_str)

# Convert set to sorted list for convenience
unique_jw_terms = sorted(list(unique_jw_terms))

print(f"Total unique JW terms: {len(unique_jw_terms)}")
# Example: print first 10 unique JW terms
for term in unique_jw_terms:
    print(term)



Generated 272 FermionOperator terms
Total unique JW terms: 99
IIII
X0 X1
X0 X1 X2 X3
X0 X1 X2 Y3
X0 X1 Y2 X3
X0 X1 Y2 Y3
X0 X1 Z2
X0 X1 Z3
X0 X2
X0 Y1
X0 Y1 X2 X3
X0 Y1 X2 Y3
X0 Y1 Y2 X3
X0 Y1 Y2 Y3
X0 Y1 Z2
X0 Y1 Z3
X0 Y2
X0 Z1 X2
X0 Z1 X2 Z3
X0 Z1 X3
X0 Z1 Y2
X0 Z1 Y2 Z3
X0 Z1 Y3
X0 Z1 Z2 X3
X0 Z1 Z2 Y3
X0 Z2 X3
X0 Z2 Y3
X1 X2
X1 X2 Z3
X1 X3
X1 Y2
X1 Y2 Z3
X1 Y3
X1 Z2 X3
X1 Z2 Y3
X2 X3
X2 Y3
Y0 X1
Y0 X1 X2 X3
Y0 X1 X2 Y3
Y0 X1 Y2 X3
Y0 X1 Y2 Y3
Y0 X1 Z2
Y0 X1 Z3
Y0 X2
Y0 Y1
Y0 Y1 X2 X3
Y0 Y1 X2 Y3
Y0 Y1 Y2 X3
Y0 Y1 Y2 Y3
Y0 Y1 Z2
Y0 Y1 Z3
Y0 Y2
Y0 Z1 X2
Y0 Z1 X2 Z3
Y0 Z1 X3
Y0 Z1 Y2
Y0 Z1 Y2 Z3
Y0 Z1 Y3
Y0 Z1 Z2 X3
Y0 Z1 Z2 Y3
Y0 Z2 X3
Y0 Z2 Y3
Y1 X2
Y1 X2 Z3
Y1 X3
Y1 Y2
Y1 Y2 Z3
Y1 Y3
Y1 Z2 X3
Y1 Z2 Y3
Y2 X3
Y2 Y3
Z0
Z0 X1 X2
Z0 X1 Y2
Z0 X1 Z2 X3
Z0 X1 Z2 Y3
Z0 X2 X3
Z0 X2 Y3
Z0 Y1 X2
Z0 Y1 Y2
Z0 Y1 Z2 X3
Z0 Y1 Z2 Y3
Z0 Y2 X3
Z0 Y2 Y3
Z0 Z1
Z0 Z2
Z0 Z3
Z1
Z1 X2 X3
Z1 X2 Y3
Z1 Y2 X3
Z1 Y2 Y3
Z1 Z2
Z1 Z3
Z2
Z2 Z3
Z3


Define parameters for molecules

In [7]:
nonzero_coeffs = {
    # H_2
    # tuple([]): -0.4196023680504887,
    # tuple(['Z0']): 0.11698671435313017,
    # tuple(['Z1']): 0.11698671435313016,
    # tuple(['Z2']): -0.0832028624164285,
    # tuple(['Z3']): -0.0832028624164285,
    # tuple(['Z0', 'Z1']): 0.14827060785303883,
    # tuple(['Z0', 'Z2']): 0.09604367370419048,
    # tuple(['Z0', 'Z3']): 0.14849154085980185,
    # tuple(['Z1', 'Z2']): 0.14849154085980185,
    # tuple(['Z1', 'Z3']): 0.09604367370419048,
    # tuple(['Z2', 'Z3']): 0.1556746362960616,
    # tuple(['X0', 'X1', 'Y2', 'Y3']): -0.05244786715561138,
    # tuple(['X0', 'Y1', 'Y2', 'X3']): 0.05244786715561138,
    # tuple(['Y0', 'X1', 'X2', 'Y3']): 0.05244786715561138,
    # tuple(['Y0', 'Y1', 'X2', 'X3']): -0.05244786715561138,

    # LiH
    tuple([]): -3.8006076768459764,
    tuple(['X0', 'X1', 'Y2', 'Y3']): -0.002137377016341704,
    tuple(['X0', 'Y1', 'Y2', 'X3']): 0.002137377016341704,
    tuple(['X0', 'Z1', 'X2']): -0.004844443306154697,
    tuple(['X0', 'Z1', 'X2', 'Z3']): -0.0132612556867148,
    tuple(['X0', 'X2']): 0.0007670968646192311,
    tuple(['Y0', 'X1', 'X2', 'Y3']): 0.002137377016341704,
    tuple(['Y0', 'Y1', 'X2', 'X3']): -0.002137377016341704,
    tuple(['Y0', 'Z1', 'Y2']): -0.004844443306154697,
    tuple(['Y0', 'Z1', 'Y2', 'Z3']): -0.0132612556867148,
    tuple(['Y0', 'Y2']): 0.0007670968646192311,
    tuple(['Z0']): 0.18330834423430795,
    tuple(['Z0', 'X1', 'Z2', 'X3']): 0.0007670968646192311,
    tuple(['Z0', 'Y1', 'Z2', 'Y3']): 0.0007670968646192311,
    tuple(['Z0', 'Z1']): 0.11344680274916535,
    tuple(['Z0', 'Z2']): 0.08829538599842374,
    tuple(['Z0', 'Z3']): 0.09043276301476544,
    tuple(['X1', 'Z2', 'X3']): -0.004844443306154701,
    tuple(['X1', 'X3']): -0.013261255686714797,
    tuple(['Y1', 'Z2', 'Y3']): -0.004844443306154701,
    tuple(['Y1', 'Y3']): -0.013261255686714797,
    tuple(['Z1']): 0.18330834423430795,
    tuple(['Z1', 'Z2']): 0.09043276301476544,
    tuple(['Z1', 'Z3']): 0.08829538599842374,
    tuple(['Z2']): 1.7703267431810716,
    tuple(['Z2', 'Z3']): 0.41464167171467575,
    tuple(['Z3']): 1.7703267431810719,
    
}

Construct Circuit

In [8]:
qubits = cirq.LineQubit.range(4) 
circuit = cirq.Circuit()

time = 0.5
n_trotter_steps = 100
dt = time / n_trotter_steps # Time per trotter step

for _ in range(n_trotter_steps):
    for term in unique_jw_terms:
        # Convert term string (like "Z0 Z1") into a list ['Z0','Z1']
        if term == "IIII":   # handle identity if present
            pauli_list = []
        else:
            pauli_list = term.split()
        
        # Look up coefficient if it’s one of the chosen terms
        coeff = nonzero_coeffs.get(tuple(pauli_list), 0.0)
        
        # Call PauliRotation only if coeff is nonzero
        PauliRotation(circuit, qubits, coeff, pauli_list, dt)
print(circuit)

                                                                                                                                                                                                                                                                                             ┌──┐                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       

In [9]:
from openfermion import haar_random_vector
from scipy.sparse.linalg import expm_multiply, expm

initial_state = haar_random_vector(2**num_qubits, 1234).astype(np.complex64)
# initial_state = np.zeros(2**num_qubits, dtype=np.complex64)
# hartree_fock_index = 15 # for LiH
# hartree_fock_index = 12 # for H_2
# initial_state[hartree_fock_index] = 1.0

exact_state = expm_multiply(-1j * time * H_mat, initial_state)

simulator = cirq.Simulator()
result = simulator.simulate(
    circuit,
    qubit_order=qubits,
    initial_state=initial_state
)
simulated_state = result.final_state_vector

print("Fidelity between exact state and intial state: ", np.abs(np.vdot(exact_state, initial_state)))
print("Fidelity between simulated state and intial state: ", np.abs(np.vdot(simulated_state, initial_state)))

# print(exact_state)
# print(simulated_state)

fidelity = np.abs(np.vdot(simulated_state, exact_state))**2
print(f"\nFinal Fidelity: {fidelity}")

Fidelity between exact state and intial state:  0.6355552842136771
Fidelity between simulated state and intial state:  0.6355317

Final Fidelity: 1.0000000620810385


Operator norm of an error

In [60]:
U_exact = expm(-1j * time * H_mat)
U_simulated = cirq.unitary(circuit)
error = U_exact - U_simulated

svd_error = np.linalg.svd(error)[1].max()
print(svd_error) # largest singular value

0.0002364341678661459
